<a href="https://colab.research.google.com/github/SKYHAWK993/LogBasedAnomalyDetection/blob/main/log_based_anomaly_detection.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
!git clone https://github.com/Thijsvanede/DeepLog.git
%cd DeepLog

Cloning into 'DeepLog'...
remote: Enumerating objects: 424, done.
remote: Counting objects: 100% (25/25), done.
remote: Compressing objects: 100% (8/8), done.
remote: Total 424 (delta 20), reused 17 (delta 17), pack-reused 399 (from 1)
Receiving objects: 100% (424/424), 1.55 MiB | 7.68 MiB/s, done.
Resolving deltas: 100% (213/213), done.
/content/DeepLog


In [2]:
!pip install tensorflow numpy pandas scikit-learn chardet
!pip install torch torchvision torchaudio --index-url https://download.pytorch.org/whl/cu118

Looking in indexes: https://download.pytorch.org/whl/cu118
INFO: pip is looking at multiple versions of torch to determine which version is compatible with other requirements. This could take a while.
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 23.2/23.2 MB 20.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 875.6/875.6 kB 32.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.1/13.1 MB 22.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 663.9/663.9 MB 2.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 417.9/417.9 MB 3.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 168.4/168.4 MB 6.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.1/58.1 MB 12.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 128.2/128.2 MB 7.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 204.1/204.1 MB 5.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 147.8/147.8 MB 7.

In [3]:
!pip install drain3
from drain3 import TemplateMiner
from drain3.template_miner_config import TemplateMinerConfig

config = TemplateMinerConfig()
#config.masking = [
#    {"regex_pattern": r"\d+", "mask_with": "<NUM>"},
#    {"regex_pattern": r"([A-Fa-f0-9]{2}-){5}[A-Fa-f0-9]{2}", "mask_with": "<MAC>"},
#]

#custom configs
config.masking = [
    {"regex_pattern": r"\d{4}-\d{2}-\d{2} \d{2}:\d{2}:\d{2}", "mask_with": "<TIMESTAMP>"},
    {"regex_pattern": r"[A-Za-z]{3} \d{1,2} \d{2}:\d{2}:\d{2}", "mask_with": "<TIMESTAMP>"},
    {"regex_pattern": r"\[\d+\]", "mask_with": "<PID>"},
    {"regex_pattern": r"\b\d{1,3}\.\d{1,3}\.\d{1,3}\.\d{1,3}\b", "mask_with": "<IP>"},
    {"regex_pattern": r"\b[a-fA-F0-9:]+:+[a-fA-F0-9:]+\b", "mask_with": "<IPv6>"},
    {"regex_pattern": r"for user \S+", "mask_with": "for user <USER>"},
    {"regex_pattern": r"port \d+", "mask_with": "port <PORT>"},
    {"regex_pattern": r":\d{2,5}", "mask_with": ":<PORT>"},
    {"regex_pattern": r"(/[^ ]+)+", "mask_with": "<FILE_PATH>"},
    {"regex_pattern": r"\b(200|301|302|400|401|403|404|500|502|503)\b", "mask_with": "<HTTP_CODE>"},
    {"regex_pattern": r"COMMAND=\S+", "mask_with": "COMMAND=<CMD>"},
    {"regex_pattern": r"USER=\S+", "mask_with": "USER=<USER>"}
]

template_miner = TemplateMiner(config=config)
log_file = "/content/Linux.log"
parsed_logs = []

import chardet

with open(log_file, "rb") as f:
    raw_data = f.read()
    result = chardet.detect(raw_data)
    print(f"Detected encoding: {result['encoding']}")

# Open the file with the detected encoding
encoding = result["encoding"]
parsed_logs = []

with open(log_file, "r", encoding=encoding, errors="replace") as f:
    for line in f:
        line = line.strip()
        result = template_miner.add_log_message(line)
        if result["change_type"]:
            print(f"New template detected: {result['template_mined']}")
        parsed_logs.append(result["template_mined"])

# Save parsed templates
templates = list(template_miner.drain.clusters)
print(f"Total templates extracted: {len(templates)}")

Streaming output truncated to the last 5000 lines.
New template detected: Dec <*> <*> combo kernel: Out of Memory: Killed process <*> <*>
New template detected: Dec <*> <*> combo kernel: Out of Memory: Killed process <*> <*>
New template detected: Dec <*> <*> combo kernel: Out of Memory: Killed process <*> <*>
New template detected: Dec <*> <*> combo kernel: Out of Memory: Killed process <*> <*>
New template detected: Dec <*> <*> combo kernel: Out of Memory: Killed process <*> <*>
New template detected: Dec <*> <*> combo kernel: Out of Memory: Killed process <*> <*>
New template detected: Dec <*> <*> combo kernel: Out of Memory: Killed process <*> <*>
New template detected: Dec <*> <*> combo kernel: Out of Memory: Killed process <*> <*>
New template detected: Dec <*> <*> combo kernel: Out of Memory: Killed process <*> <*>
New template detected: Dec <*> <*> combo kernel: Out of Memory: Killed process <*> <*>
New template detected: Dec <*> <*> combo kernel: Out of Memory: Killed process 

In [4]:
template_id_map = {template: idx for idx, template in enumerate(templates)}
log_sequences = []

for template in parsed_logs:
    #cechkk if the template is present in the template_id_map
    if template in template_id_map:
        log_sequences.append(template_id_map[template])
    else:
        log_sequences.append(len(template_id_map))
        #add the unseen template to template_id_map
        template_id_map[template] = len(template_id_map)


#create sliding window sequences
window_size = 15  #eka velela kiti log uids ghetay model, update to 15
X, y = [], []

for i in range(len(log_sequences) - window_size):
    X.append(log_sequences[i:i + window_size])
    y.append(log_sequences[i + window_size])

import numpy as np
X = np.array(X)
y = np.array(y)

#training 80%, testing 20%
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

In [5]:
import torch
import torch.nn as nn

class DeepLog(nn.Module):
    def __init__(self, num_classes, hidden_size=64, num_layers=2, window_size=10):
        super(DeepLog, self).__init__()
        self.hidden_size = hidden_size
        self.num_layers = num_layers
        self.window_size = window_size

        #Embedding
        self.embedding = nn.Embedding(num_classes, hidden_size)

        #LSTM
        self.lstm = nn.LSTM(
            input_size=hidden_size,
            hidden_size=hidden_size,
            num_layers=num_layers,
            batch_first=True,
            dropout=0.3
        )

        #Fully connected layer
        self.fc = nn.Linear(hidden_size, num_classes)

    def forward(self, x):
        x = self.embedding(x)
        h0 = torch.zeros(self.num_layers, x.size(0), self.hidden_size).to(x.device)
        c0 = torch.zeros(self.num_layers, x.size(0), self.hidden_size).to(x.device)
        #fwd pass
        out, _ = self.lstm(x, (h0, c0))
        out = self.fc(out[:, -1, :])
        return out

In [6]:
import numpy as np
from sklearn.model_selection import train_test_split
X_train = torch.tensor(X_train, dtype=torch.long)
y_train = torch.tensor(y_train, dtype=torch.long)
X_test = torch.tensor(X_test, dtype=torch.long)
y_test = torch.tensor(y_test, dtype=torch.long)

In [7]:
model = DeepLog(
    num_classes=len(template_id_map),  #unique log template num
    hidden_size=256,              #lstm hidden state size
    num_layers=4,                #lstm layers num
    window_size=window_size
)

criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(model.parameters(), lr=0.001, weight_decay=1e-4)

num_epochs = 10
batch_size = 64

for epoch in range(num_epochs):
    model.train()
    for i in range(0, len(X_train), batch_size):
        inputs = X_train[i:i + batch_size]
        labels = y_train[i:i + batch_size]
        outputs = model(inputs)
        loss = criterion(outputs, labels)
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

    print(f"Epoch [{epoch + 1}/{num_epochs}], Loss: {loss.item():.4f}")

Epoch [1/10], Loss: 1.7562
Epoch [2/10], Loss: 1.2901
Epoch [3/10], Loss: 0.7821
Epoch [4/10], Loss: 0.5709
Epoch [5/10], Loss: 0.4234
Epoch [6/10], Loss: 0.3815
Epoch [7/10], Loss: 0.3421
Epoch [8/10], Loss: 0.2351
Epoch [9/10], Loss: 0.1975
Epoch [10/10], Loss: 0.1949


In [8]:
model.eval()
total_loss = 0.0

criterion = nn.CrossEntropyLoss()

with torch.no_grad():
    outputs = model(X_test)
    _, predicted = torch.max(outputs, 1)
    accuracy = (predicted == y_test).float().mean()  # Compute accuracy

    # Compute validation loss
    loss = criterion(outputs, y_test)
    total_loss += loss.item()

    print(f"Test Accuracy: {accuracy.item():.4f}")
    print(f"Validation Loss: {total_loss:.4f}")  # Print validation loss

anomalies = predicted != y_test
print(f"Total anomalies detected: {sum(anomalies).item()}")


Test Accuracy: 0.8376
Validation Loss: 1.1388
Total anomalies detected: 830


In [ ]:
# Find indices of anomalies
anomalous_indices = torch.nonzero(anomalies).squeeze().tolist()
# Reverse mapping of event IDs to log templates
id_to_template = {v: k for k, v in template_id_map.items()}
print("\nDetected Anomalous Logs:\n")
for idx in anomalous_indices:
    actual_event_id = y_test[idx].item()
    predicted_event_id = predicted[idx].item()

    actual_template = id_to_template.get(actual_event_id, "Unknown Template")
    predicted_template = id_to_template.get(predicted_event_id, "Unknown Template")

    print(f"Index: {idx}")
    print(f"Actual Log Template  : {actual_template}")
    print(f"Predicted Log Template: {predicted_template}")
    print("-" * 80)



Detected Anomalous Logs:

Index: 4
Actual Log Template  : Dec 9 <*> combo syslog: <*> shutdown succeeded
Predicted Log Template: Dec 9 09:43:21 combo syslogd 1.4.1: restart.
--------------------------------------------------------------------------------
Index: 6
Actual Log Template  : Nov <*> <*> combo kernel: Out of Memory: Killed process <*> <*>
Predicted Log Template: Nov <*> <*> combo <*> authentication failure; logname= uid=0 euid=0 tty=NODEVssh ruser= <*>
--------------------------------------------------------------------------------
Index: 12
Actual Log Template  : Sep 19 05:57:42 combo kernel: <*> <*> <*> <*> <*> <*>
Predicted Log Template: Sep 19 <*> combo kernel: <*> <*> <*> <*> <*>
--------------------------------------------------------------------------------
Index: 13
Actual Log Template  : Nov <*> <*> combo kernel: httpd: page allocation failure. order:0, <*>
Predicted Log Template: Nov <*> <*> combo kernel: Out of Memory: Killed process <*> <*>
----------------------

In [ ]:
import matplotlib.pyplot as plt
import seaborn as sns

# Ensure seaborn has a clean style
sns.set(style="whitegrid")

# Convert tensors to numpy for plotting
y_test_np = y_test.numpy()
predicted_np = predicted.numpy()
anomalous_indices = np.where(y_test_np != predicted_np)[0]

# Reverse mapping of event IDs to log templates
id_to_template = {v: k for k, v in template_id_map.items()}

# Plot 1: Actual vs. Predicted Log Event IDs
#plt.figure(figsize=(12, 6))
#plt.plot(range(len(y_test_np)), y_test_np, label="Actual Event ID", color="blue", alpha=0.6)
#plt.plot(range(len(predicted_np)), predicted_np, label="Predicted Event ID", color="red", linestyle="dashed", alpha=0.6)
#plt.scatter(anomalous_indices, y_test_np[anomalous_indices], color="black", marker='x', label="Anomalies")
#
#plt.xlabel("Log Sequence Index")
#plt.ylabel("Event ID")
#plt.title("Actual vs Predicted Log Event IDs with Anomalies")
#plt.legend()
#plt.show()
#
## Plot 2: Anomalies Highlighted on the Timeline
#plt.figure(figsize=(12, 5))
#plt.plot(range(len(y_test_np)), y_test_np, label="Log Event IDs", color="gray", alpha=0.4)
#plt.scatter(anomalous_indices, y_test_np[anomalous_indices], color="red", label="Anomalies", marker='x')
#
#plt.xlabel("Log Sequence Index")
#plt.ylabel("Event ID")
#plt.title("Anomaly Detection in Log Sequences")
#plt.legend()
#plt.show()

# Plot 3: Anomaly Count per Event ID
anomalous_events = y_test_np[anomalous_indices]
anomaly_counts = {id_to_template[event_id]: list(anomalous_events).count(event_id) for event_id in set(anomalous_events)}

# Sort by most frequent anomalies
sorted_anomalies = sorted(anomaly_counts.items(), key=lambda x: x[1], reverse=True)

# Extract names and counts for plotting
event_names = [item[0] for item in sorted_anomalies]
event_counts = [item[1] for item in sorted_anomalies]

# Bar plot
plt.figure(figsize=(50, 50))
sns.barplot(x=event_counts, y=event_names, palette="Reds_r")
plt.xlabel("Number of Anomalies Detected")
plt.ylabel("Log Event Template")
plt.title("Most Frequently Anomalous Log Events")
plt.savefig("most_frequent_anomalies.png")








<ipython-input-19-bb9f5d770b2e>:51: FutureWarning: 

Passing `palette` without assigning `hue` is deprecated and will be removed in v0.14.0. Assign the `y` variable to `hue` and set `legend=False` for the same effect.

  sns.barplot(x=event_counts, y=event_names, palette="Reds_r")
